In [0]:
sas_token = "sp=rcwl&st=2026-01-02T23:25:54Z&se=2026-01-28T07:40:54Z&spr=https&sv=2024-11-04&sr=c&sig=T2m3SUYqJPnkxFmRzrnCeKviOcAidCnff%2B58bN5E1XE%3D"
storage_account_name = "newadbprojektkakastorage"
container_name = "data"

spark.conf.set(
    f"fs.azure.account.auth.type.{storage_account_name}.dfs.core.windows.net", "SAS"
)
spark.conf.set(
    f"fs.azure.sas.token.provider.type.{storage_account_name}.dfs.core.windows.net",
    "org.apache.hadoop.fs.azurebfs.sas.FixedSASTokenProvider"
)
spark.conf.set(
    f"fs.azure.sas.fixed.token.{storage_account_name}.dfs.core.windows.net",
    sas_token
)

base_path = f"abfss://{container_name}@{storage_account_name}.dfs.core.windows.net"
print(f"Skonfigurowano dostęp do: {base_path}")

Skonfigurowano dostęp do: abfss://data@newadbprojektkakastorage.dfs.core.windows.net


In [0]:
df_model = spark.read.format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load(f"{base_path}/final_results/df_weather_jfk.csv")

display(df_model.limit(5))

DAY_OF_WEEK AIRLINE FLIGHT_NUMBER DEPARTURE_DELAY DISTANCE CANCELLED ORIGIN_AIRPORT WEATHER_DELAY ScheduledTimestamp DeparturedTimestamp HOURLYPrecip HOURLYVISIBILITY HOURLYWindSpeed 1 DL 2338 -3 1069 0 JFK null 2015-01-05T16:00:00Z 2015-01-05T15:57:00Z 0.0 10.0 15.0 1 AA 67 9 1598 0 JFK null 2015-01-05T16:05:00Z 2015-01-05T16:14:00Z 0.0 10.0 15.0 1 AA 65 5 1391 0 JFK null 2015-01-05T16:15:00Z 2015-01-05T16:20:00Z 0.0 10.0 15.0 1 VX 27 2 2586 0 JFK null 2015-01-05T16:30:00Z 2015-01-05T16:32:00Z 0.0 10.0 15.0 1 AA 133 0 2475 0 JFK null 2015-01-05T16:30:00Z 2015-01-05T16:30:00Z 0.0 10.0 15.0

In [0]:
from pyspark.ml.feature import StringIndexer, VectorAssembler, StandardScaler
from pyspark.ml import Pipeline
from pyspark.sql.functions import col

#usuwamy kolumny czasowe/identyfikatory, zostawiamy parametry lotu i pogody
feature_cols = ["DISTANCE", "HOURLYVISIBILITY", "HOURLYWindSpeed", "DAY_OF_WEEK"]

#linie lotnicze (tekst na liczby)
airline_indexer = StringIndexer(inputCol="AIRLINE", outputCol="AIRLINE_INDEX", handleInvalid="skip")

#składanie cech w jeden wektor
assembler = VectorAssembler(inputCols=feature_cols + ["AIRLINE_INDEX"], outputCol="raw_features", handleInvalid="skip")

#skalowanie 
scaler = StandardScaler(inputCol="raw_features", outputCol="features")

In [0]:
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.evaluation import BinaryClassificationEvaluator

train_data, test_data = df_model.randomSplit([0.8, 0.2], seed=123)

rf_class = RandomForestClassifier(labelCol="CANCELLED", featuresCol="features", numTrees=50)

#pipeline dla klasyfikacji
pipeline_class = Pipeline(stages=[airline_indexer, assembler, scaler, rf_class])
model_cancel = pipeline_class.fit(train_data)

#predykcja
predictions_cancel = model_cancel.transform(test_data)

#AUC - im bliżej 1, tym lepiej
evaluator_auc = BinaryClassificationEvaluator(labelCol="CANCELLED", metricName="areaUnderROC")
auc = evaluator_auc.evaluate(predictions_cancel)

print(f"Skuteczność modelu (AUC) dla odwołań: {auc}")
display(predictions_cancel.select("CANCELLED", "prediction", "probability"))

Skuteczność modelu (AUC) dla odwołań: 0.9946198830409356


CANCELLED prediction probability 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998425696632295, 1.5743033677053945E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998418123040469, 1.58187695953072E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998193785919172, 1.806214080827974E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998175441216679, 1.824558783320674E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998446414221843, 1.5535857781572753E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998153777438517, 1.846222561483586E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998425696632295, 1.5743033677053945E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998153777438517, 1.846222561483586E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998192839730556, 1.8071602694427663E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9995425958982176, 4.574041017824057E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.999842475044368, 1.575249556320187E-4)) 0 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9998425696632295, 1.5743033677053945E-4)) 0 0.0 Ma

In [0]:
from pyspark.ml.regression import GBTRegressor
from pyspark.ml.evaluation import RegressionEvaluator

df_reg = df_model.filter(col("CANCELLED") == 0)
train_reg, test_reg = df_reg.randomSplit([0.8, 0.2], seed=123)

gbt_reg = GBTRegressor(labelCol="DEPARTURE_DELAY", featuresCol="features", maxIter=20)

#pipeline dla regresji
pipeline_reg = Pipeline(stages=[airline_indexer, assembler, scaler, gbt_reg])
model_delay = pipeline_reg.fit(train_reg)

#predykcja
predictions_delay = model_delay.transform(test_reg)

#RMSE
evaluator_rmse = RegressionEvaluator(labelCol="DEPARTURE_DELAY", predictionCol="prediction", metricName="rmse")
rmse = evaluator_rmse.evaluate(predictions_delay)

print(f"Średni błąd przewidywania (RMSE): {rmse} minut")
display(predictions_delay.select("DEPARTURE_DELAY", "prediction"))

Średni błąd przewidywania (RMSE): 5.195487208727045 minut


DEPARTURE_DELAY prediction -6 -2.8135583020444463 -6 -2.891414167750666 -5 -2.8135583020444463 5 -2.52226078882262 -7 -3.6593851929929273 -6 -2.864223686678583 -3 -2.8135583020444463 -6 -2.795178608323851 -6 -2.8135583020444463 -3 -2.864223686678583 -1 -1.7935568494177563 1 -2.249348069765118 12 -1.8462937551090444 0 1.7223541946593952 -6 -1.0736913641901593 5 -1.2478227805959832 -4 -2.0887271338439883 0 -2.2298331779297564 -8 -2.006098722086017 -6 -1.6147932447559565 -3 -1.665458629390093 2 -1.5964135510353608 -4 -2.864223686678583 -8 -1.3302175934389124 1 -2.6178937801851005 2 -2.909191293406927 8 -2.2198067605547696 -8 -2.8135583020444463 -6 -2.93407856356369 -5 -2.713713868533942 -4 -2.8135583020444463 -3 -2.8908115996863315 -7 -2.8908115996863315 -6 -3.0971438619151503 -5 -2.8908115996863315 -5 -2.032865236755017 -4 -2.864223686678583 0 -2.8135583020444463 2 -2.144303608712542 -3 -2.795178608323851 -3 -2.52226078882262 -1 -2.8135583020444463 -7 -2.4625065863829114 -3 -2.7250074506595254 -2 -2.0887271338439883 0 -1.6064838233497607 -6 -1.2853751940164615 11 -1.0124573745152305 4 -1.6204037667413371 0 -2.795178608323851 -3 -1.0355659155138452 0 -2.795178608323851 1 -2.8135583020444463 -7 -1.6461047261819168 -6 -1.209697331919669 -1 -1.6094383926407025 1 -1.6064838233497607 -5 -1.209697331919669 -5 -1.0355659155138452 2 -2.109312916410513 -7 -1.0355659155138452 -2 -1.209697331919669 3 -1.7930173434361991 -1 -1.224419430727288 -1 -2.169342489005275 -6 -2.0422102489598193 -7 -1.0736913641901593 -5 -1.237656960546297 -3 -1.3249369111020552 -8 -1.1991053448072362 -5 -2.404760647612451 -2 -2.128827808245875 -3 -0.5998394899037869 -4 -1.0355659155138452 1 -1.0355659155138452 16 -0.5998394899037869 -5 -1.6214588034382382 5 -1.65270073622896 -8 -0.9785184403408221 -2 -1.1991053448072362 -2 -2.80935631672449 6 -2.8932912428803217 -5 -1.0355659155138452 -1 -1.209697331919669 -4 -0.5427920147307636 -3 -0.5998394899037869 6 -0.5998394899037869 -5 -1.209697331919669 -4 -1.0820828003980147 -8 -2.762839431840321 -2 -2.8932912428803217 5 -2.8698185607924884 10 -1.5474642205112024 -7 -0.6304856736435771 -1 -0.5409759687592787 -6 -0.993221074120031 2 -0.8760480025037124 -8 -0.20569439716634816 -2 -0.20569439716634816 -5 -0.20569439716634816 6 0.1776759763233456 -2 0.9684044977277003 -1 -0.472909035257342 2 -0.5562063785931162 2 -0.472909035257342 -3 -0.08438384633772722 -2 -0.16259951403711845 8 -0.20569439716634816 5 -1.1909408049770396 -4 -1.9756165433260227 -7 -1.7669502588376882 -4 -2.086447811978582 -3 -0.8760480025037124 0 -0.7893322563304326 -3 -0.34757618876441976 1 -0.2973989022503245 1 -0.718735735041614 1 -0.8812597154884991 -7 -0.8458861277843945 -6 -0.32540812014594567 -2 -0.16259951403711845 16 -0.4360266023087795 -4 -1.83110582581608 -2 -1.733254142006183 -5 -0.17637008920847666 0 0.06465418459974176 -3 -0.8787473359556691 -7 -0.9012936149619643 3 -0.39146553731102923 0 -0.16259951403711845 0 -0.02698128800415856 -7 -2.0143373676612133 -6 -1.9397558086660502 -5 -2.5139956455955295 -1 -1.6355702022406526 -1 -1.9101388347646968 1 -1.6355702022406526 -7 -0.7893322563304326 10 -0.3933966341189942 10 -0.8760480025037124 -7 -0.5266395659384747 -6 -0.7137815509498809 -7 -0.5112886642260006 -1 -0.34436627140858816 -2 -0.715748794518042 -1 -1.135216855411453 -6 -1.4440008975827314 -6 -1.5308356349319214 -4 -0.8458861277843945 1 -0.6283470096722762 -3 -0.472909035257342 -2 -0.7190149847019434 -5 -1.9756165433260227 -1 -1.9397558086660502 -6 -1.718771309526929 -4 -1.9397558086660502 -3 -2.0143373676612133 -2 -2.0143373676612133 -4 -0.8423518856722074 15 -0.8760480025037124 -6 -0.8276649675519139 -3 -1.4440008975827314 -1 -0.02698128800415856 4 -0.02698128800415856 8 -0.8276649675519139 -2 -0.7309667936797901 -1 -0.20174170309083242 -5 -0.02698128800415856 10 0.11866015979121512 -7 -2.086447811978582 -1 -2.4523413801591727 -8 -1.4440008975827314 -7 -0.8276649675519139 -6 -0.7137815509498809 0 -0.8276649675519139 -7 -0.07611759980562213 -2 

In [0]:
display(predictions_cancel.filter((col("prediction") == 1) | (col("CANCELLED") == 1))
        .select("CANCELLED", "prediction", "probability"))

CANCELLED prediction probability 1 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.9979509447254309, 0.002049055274569105))